In [1]:
import spacy_transformers
import pandas as pd
import re
import spacy
import textacy
import visualise_spacy_tree
import glob
from spacy.matcher import Matcher 
import os
import sys
import nltk
import en_core_web_trf
import re
from pathlib import Path
from pprint import pprint
from sklearn_crfsuite import CRF
from nltk.corpus import opinion_lexicon
from spacy.matcher import Matcher
from nltk import pos_tag
from nltk.tokenize import word_tokenize
from sklearn_crfsuite import metrics
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
import seaborn as sns

import numpy as np
from collections import defaultdict
from collections import Counter

c:\Users\zaloke\Documents\python\Lenguaje_natural\env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Users\zaloke\Documents\python\Lenguaje_natural\env\Lib\site-packages\transformers\utils\generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
c:\Users\zaloke\Documents\python\Lenguaje_natural\env\Lib\site-packages\transformers\utils\generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [2]:
pd.set_option('display.max_colwidth', 2000)
pd.options.display.max_rows=100

In [3]:
dtype_dict = {
    'AppID': 'int64',
    'name': 'object',
    'release_date': 'object',
    'required_age': 'object',
    'price': 'float64',
    'dlc_count': 'float64',
    'detailed_description': 'object',
    'about_the_game': 'object',
    'short_description': 'object',
    'reviews': 'object',
    'header_image': 'object',
    'website': 'object',
    'support_url': 'object',
    'support_email': 'object',
    'windows': 'object',
    'mac': 'object',
    'linux': 'object',
    'metacritic_score': 'object',
    'metacritic_url': 'object',
    'achievements': 'object',
    'recommendations': 'object',
    'notes': 'object',
    'supported_languages': 'object',
    'full_audio_languages': 'object',
    'packages': 'object',
    
    'Unnamed: 87': 'float64',
    'Unnamed: 88': 'float64',
    'Unnamed: 89': 'float64'
}


In [4]:
df = pd.read_csv('games_may2024_cleaned_text.csv',  dtype=dtype_dict, low_memory=False)
df = df[[ "about_the_game", "short_description","genres", "supported_languages"]]
print(df.head())

In [5]:
nlp = spacy.load('en_core_web_sm')

def extraer_terminos_clave(texto):
    doc = nlp(texto)
    palabras_filtradas = [token.text for token in doc if not token.is_stop and token.is_alpha]
    return palabras_filtradas

In [6]:
palabras = []

for chunk in pd.read_csv('games_may2024_cleaned_text.csv', chunksize=1000):
    for texto in chunk['about_the_game']:
        if pd.notna(texto):
            palabra = extraer_terminos_clave((str)(texto))
            palabras.extend(palabra)

palabras_unidas = ' '.join(palabras)

In [8]:
nlp.max_length = 1500000  # Aumenta el límite de caracteres permitido

# Función para dividir el texto en fragmentos manejables
def dividir_texto(texto, n=100000):
    """Divide el texto en fragmentos de n caracteres."""
    for i in range(0, len(texto), n):
        yield texto[i:i + n]

In [9]:
# Divide el texto en fragmentos más pequeños
fragmentos = list(dividir_texto(palabras_unidas, n=100000))

# Inicializa un Counter para los términos clave
contador_terminos = Counter()

# Procesa cada fragmento y extrae términos clave con textacy
for fragmento in fragmentos:
    doc = textacy.make_spacy_doc(fragmento, lang='en_core_web_lg')
    keyterms = textacy.extract.keyterms.textrank(doc, topn=100)
    contador_terminos.update([term for term, _ in keyterms])

# Extrae los términos clave más comunes
terminos_clave = dict(contador_terminos)

# Imprime los términos clave
print("Términos clave más comunes:", terminos_clave)

Términos clave más comunes: {'separate campaign unique story test chamber new player character new mode force player': 1, 'realistic survival online multiplayer survival persistent player run server local player splitscreen coop hundred zombie swarm mechanic indepth visual hearing system line sight system realtime lighting sound visibility mechanic': 1, 'unforgiving postapocalyptic world overrun undead day openworld game unique combination firstperson shooter survival horror tower defense roleplaying game': 1, 'game game length game length little bit shortish game': 1, 'new match mission new fragmentscollection system new seasonal play': 1, 'rate unlockable cosmetic skin game year game award good action game ign award nomination': 1, 'world los santos blaine county resolution chance experience game running frame second game': 1, 'free game time popular online action game time team fortress': 1, 'close zombie new survivor new story new dialogue expansive campaign cooperative': 1, 'trave

In [11]:
terminos_clave_mas_comunes = contador_terminos.most_common()

In [12]:
# Guardar los términos clave en un archivo JSON
import json
with open('terminos_clave_mas_comunes.json', 'w', encoding='utf-8') as file:
    json.dump(terminos_clave_mas_comunes, file, ensure_ascii=False, indent=4)

In [14]:
from spacy.training import Example  # Asegúrate de importar Example

# Cargar el modelo de spaCy
nlp = spacy.load("en_core_web_sm")

# Función para procesar texto y extraer entidades
def extraer_entidades(texto):
    doc = nlp(texto)
    entidades = [(ent.start_char, ent.end_char, ent.label_) for ent in doc.ents]
    return entidades

# Cargar los archivos de texto en DataFrames
df_columna2 = pd.read_csv('df_cleaned_genres.txt', header=None, names=['texto'])

# Procesar los textos y extraer entidades
df_columna2['entidades'] = df_columna2['texto'].apply(extraer_entidades)

# Convertir los datos a formato JSON para spaCy
def convertir_a_json(df):
    datos_transformados = []
    for _, row in df.iterrows():
        texto = row['texto']
        anotaciones = {"entities": row['entidades']}
        datos_transformados.append((texto, anotaciones))
    return datos_transformados

# Convertir DataFrame a formato de entrenamiento
datos_entrenamiento = convertir_a_json(df_columna2)

# Guardar en archivo JSON
with open('terminos_clave.json', 'w', encoding='utf-8') as file:
    json.dump(datos_entrenamiento, file, ensure_ascii=False, indent=4)

# Configuración para entrenar el modelo NER
def entrenar_modelo_ner(datos_json):
    # Cargar un modelo base
    nlp = spacy.load('en_core_web_sm')
    
    # Añadir el componente NER al pipeline si no está presente
    if 'ner' not in nlp.pipe_names:
        ner = nlp.add_pipe('ner')
    else:
        ner = nlp.get_pipe('ner')
    
    # Añadir etiquetas al componente NER
    for _, annotations in datos_json:
        for ent in annotations.get('entities'):
            ner.add_label(ent[2])
    
    # Preparar datos para el entrenamiento
    def crear_ejemplos(data, nlp):
        ejemplos = []
        for texto, annot in data:
            doc = nlp.make_doc(texto)
            ejemplo = Example.from_dict(doc, annot)
            ejemplos.append(ejemplo)
        return ejemplos
    
    # Crear ejemplos
    ejemplos = crear_ejemplos(datos_json, nlp)
    
    # Entrenamiento
    optimizer = nlp.begin_training()
    for epoch in range(10):  # Número de épocas
        random.shuffle(ejemplos)
        losses = {}
        for ejemplo in ejemplos:
            nlp.update([ejemplo], drop=0.5, losses=losses, sgd=optimizer)
        print(f"Época {epoch + 1}, Pérdida: {losses}")
    
    # Guardar el modelo entrenado
    nlp.to_disk('modelo_ner_entrenado')

# Entrenar el modelo NER con los datos preparados
entrenar_modelo_ner(datos_entrenamiento)
